
<a id='chap-tpgraphespetitsmondes'></a>

# Travaux pratiques - Fouille de réseaux sociaux, deuxième partie

## Environnement de travail

Références externes utiles :

- [Documentation Spark](https://spark.apache.org/docs/latest/)  
- [Démarrage avec les DataFrames Spark en Python](https://spark.apache.org/docs/latest/api/python/getting_started/quickstart_df.html)  
- [Documentation API Spark en Python](https://spark.apache.org/docs/latest/api/python/index.html)  
- [Tutoriel Spark avec exemples](https://sparkbyexamples.com/pyspark-tutorial/)  
- [Site langage Python](https://www.python.org/)  

## Introduction aux réseaux Petits Mondes

C’est notamment avec l’avènement de l’Internet (puis du Web et des réseaux
sociaux en ligne) que des graphes de grande taille ont été collectés, permettant
d’observer la formation de réseaux réels. Il est rapidement apparu que ces
derniers avaient des propriétés différentes de celles des modèles idéaux étudiés
en théorie des graphes traditionnelle. L’un des premiers articles sur le sujet,
publié en 1998 par Duncan Watts et Steven Strogatz, s’appelait « Collective
dynamics of small world networks », et présentait un premier modèle mathématique
disposant des propriétés observées sur ces graphes de terrain, à savoir :

1. la plupart des nœuds ont un degré faible et appartiennent à un sous-ensemble
  dense de nœuds (autrement dit : une fraction importante des voisins d’un nœud
  sont connectés entre eux, ou encore : « mes amis sont amis entre eux ») ;  
1. malgré cette première propriété, il est possible d’atteindre n’importe quel
  autre nœud du graphe assez facilement, c’est-à-dire en passant par un faible
  nombre d’intermédiaires (mathématiquement, cela correspond à une moyenne des
  plus courts chemins faible).  


Depuis cet article originel, des réseaux réels ont été étudiés dans des domaines
très variés et nombre d’entre eux possèdent ces propriétés : on les appelle des
« réseaux petits mondes ».

## Objectifs du TP

Dans un premier temps, on poursuit l’étude abordée dans la séance précédente, en
examinant la structure du graphe après avoir proposé un filtrage des nœuds.

Ensuite, on s’intéresse à une métrique définie par Watts et Strogatz permettant
de voir à quel point les deux propriétés ci-dessus sont vraies pour le graphe
étudié. Nous allons utiliser GraphX pour effectuer ce calcul, qui repose sur le
nombre de triangles.

## Filtrer le graphe

### Revenir à l’état de la fin de la séance précédente

Voici la liste des commandes que vous devez saisir pour revenir rapidement à la
fin de la première séance.

> > 

In [ ]:
import os

# Crée un dossier data
dossier_tp = "tpgraphes/medline_data/"
fichier_xml_a = dossier_tp + "medsamp2016a.xml"

if not os.path.exists(fichier_xml_a):
  os.system("mkdir -p tpgraphes/medline_data")

  # Télécharge les données Medline
  sortie = "téléchargement OK" if os.system("wget -q -nc ftp://ftp.nlm.nih.gov/nlmdata/sample/medline/medsamp2016*.xml.gz -P tpgraphes/medline_data") == 0 else "problème avec le téléchargement des fichiers"
  print(sortie)
else:
  print("fichiers de données présents dans " + dossier_tp)

Décompressons les fichiers et regardons leur taille.

In [ ]:
if not os.path.exists(fichier_xml_a):
  os.system("gunzip tpgraphes/medline_data/*gz")

In [ ]:
!ls -lh tpgraphes/medline_data/*xml

In [ ]:
# récupère le lsa.jar
os.system("mkdir -p tpgraphes/jars")
os.system("wget -nv -nc http://cedric.cnam.fr/~ferecatu/RCP216/tp/tptexte/lsa.jar -P tpgraphes/jars")
# récupère spark-xml
os.system("wget -nv -nc http://cedric.cnam.fr/vertigo/Cours/RCP216/docs/spark-xml_2.11-0.9.0.jar -P tpgraphes/jars")

In [ ]:
import sys
os.environ['PYSPARK_PYTHON'] = sys.executable
os.environ['PYSPARK_DRIVER_PYTHON'] = sys.executable
os.environ['PYSPARK_SUBMIT_ARGS'] = '--jars /home/jovyan/MonDossier/tpgraphes/jars/spark-xml_2.11-0.9.0.jar --packages graphframes:graphframes:0.8.1-spark3.0-s_2.12 pyspark-shell'

In [ ]:
from pyspark.conf import SparkConf
from pyspark.sql.session import SparkSession
from pyspark.context import SparkContext
conf = SparkConf().set("spark.jars", "tpgraphes/jars/lsa.jar, tpgraphes/jars/spark-xml_2.11-0.9.0.jar")
sc = SparkContext.getOrCreate(conf=conf)
spark = SparkSession.builder.getOrCreate()

In [ ]:
def loadMedline(path):
  temp = sc.newAPIHadoopFile(
  path,
  'com.databricks.spark.xml.XmlInputFormat',
  'org.apache.hadoop.io.LongWritable',
  'org.apache.hadoop.io.Text',
  conf={
      'xmlinput.start':'<MedlineCitation ',
      'xmlinput.end':'</MedlineCitation>',
      'xmlinput.encoding': 'utf-8'})
  return temp

In [ ]:
rdds = {}
for letter in "abcdefgh":
   rdds[letter] = loadMedline("tpgraphes/medline_data/medsamp2016"+letter+".xml")

medline_raw = rdds["a"].union(rdds["b"]).union(rdds["c"]).union(rdds["d"]).union(rdds["e"]).union(rdds["f"]).union(rdds["g"]).union(rdds["h"])

In [ ]:
import xml.etree.ElementTree as ET
def majorTopics(string):
    mtlist = []
    elem = ET.fromstring(string) # devient du XML
    for descriptor in elem.iter('DescriptorName'):
        if descriptor.attrib['MajorTopicYN'] == 'Y':
            mtlist.append(descriptor.text)
    return mtlist

medline = medline_raw.map(lambda t: majorTopics(t[1]))
topics = medline.flatMap(lambda l: l)

In [ ]:
from operator import add
from itertools import combinations
topicPairs = medline.flatMap(lambda l: combinations(sorted(l),2))
cooccurs = topicPairs.map(lambda p: (p, 1)).reduceByKey(add)
cooccurs.cache()

In [ ]:
from pyspark.sql.types import StructType,StructField, StringType, IntegerType
edges_schema = StructType([
    StructField('src', StringType(), True),
    StructField('dst', StringType(), True),
    StructField('freq', IntegerType(), True)
])
edges = spark.createDataFrame(data = cooccurs.map(lambda l: (l[0][0],l[0][1],l[1])), schema = edges_schema)

In [ ]:
tmp_vert = topics.map(lambda t: (t,(hash(t)) ))
vertices_schema = StructType([
    StructField('id', StringType(), True),
    StructField('hash', StringType(), True),
     ])
vertices = spark.createDataFrame(data = tmp_vert, schema = vertices_schema)

In [ ]:
from graphframes import *
topicGraph = GraphFrame(vertices, edges)
topicGraph.cache()

In [ ]:
degrees = topicGraph.degrees
d = degrees.select("degree").rdd.flatMap(lambda x:x)
freqDegres = d.countByValue()
# on obtient le nombre de sommets de degrés n
distribDegres = sorted(freqDegres.items(), key=lambda item: item[0], reverse=True)

In [ ]:
from pyspark.sql.functions import *
topicGraph.degrees.orderBy('degree', ascending=False).show(10)

In [ ]:
!mkdir checkpoints
spark.sparkContext.setCheckpointDir('checkpoints')
# calcul des composantes connexes du graphe
result = topicGraph.connectedComponents()

In [ ]:
resrdd = result.select('component').rdd
from pyspark.sql import Row
temp = resrdd.map(lambda row: row['component'])
cc = temp.countByValue()

cc_sorted = sorted(cc.items(), key=lambda item: item[1], reverse=True)
for k,v in enumerate(cc_sorted[:10]):
   print(k+1, v[0], "nb noeuds:", v[1])



### Une nouvelle pondération

Dans notre graphe, les arêtes sont pour le moment pondérées par le nombre de
fois qu’une paire de concepts est apparue dans les différents articles (si A et
B sont apparus dans ensemble dans 216 articles, l’arête A-B a pour attribut
216). On n’a pas utilisé cette valeur auparavant.

En construisant le graphe comme on l’a fait, on n’a donc pas distingué quelles
sont les paires de concepts utilisées conjointement car elles ont un sens
ensemble, et celles qui apparaissent fréquemment dans tous les documents.
(pensez par analogie avec la fréquence seule des mots dans de la fouille de
texte, et à l’amélioration fournie par le score TF-IDF). Nous allons donc
rechercher une manière de pondérer qui tienne compte de cela, en essayant
d’évaluer dans quelle mesure la co-occurrence de deux sujets est
**intéressante**. On va utiliser pour cela un test du \${\chi}^2\$
pour mesurer si l’occurence d’un concept est indépendante de celle
d’un autre (et préserver les paires de concepts non indépendants). Vous
trouverez sur [Wikipedia](http://fr.wikipedia.org/wiki/Test_du_%CF%87%C2%B2)
un rappel de ce qu’est un test de \${\chi}^2\$, il sera
utilisé ici dans sa [variante corrigée par F. Yates](https://en.wikipedia.org/wiki/Yates%27s_correction_for_continuity).

Pour une paire (A,B) de concepts, on a la table de contingence suivante qui
représente les co-occurrences des majorsTopics dans notre base Medline :

|| Oui B  | Non B  | Total A  |
| :- | -: | :-: |:-: |
|** Oui A **    | OO     | ON     | OA       |
|** Non A **    | NO     | NN     | NA       |
|** Total B **  | OB     | NB     | T        |

Dans cette table, OO, ON, NO et NN représentent les valeurs brutes de
présence/absence des concepts A et B. OA et NA désignent les sommes pour des
lignes pour le concept A (respectivement OB, NB pour B). T est le nombre total
de documents. Pour notre test \${\chi}^2\$, on suppose OO, ON, NO et NN
tirés d’une distribution inconnue. On calcule la valeur du \${\chi}^2\$ à
partir de ces valeurs avec la formule suivante :

$$
\chi^2 = T \frac{(OO * NN - ON * NO)^2}{OA * NA * OB * NB}
$$

Si nos concepts sont indépendants, on peut s’attendre à ce que la valeur obtenue
soit celle d’une loi de \${\chi}^2\$ avec le nombre de degrés de liberté
approprié. Ici, le nombre de degrés de liberté est \${\chi}^2\$.

Une valeur plus élevée indique que les variables ont **moins de chances d’être
indépendantes**, ce qui pour nous caractérise une paire intéressante de
concepts, que l’on souhaitera conserver.

>**Note**
>
>plus précisément, la p-value associée la distribution (CDF) du
\${\chi}^2\$ à un degré de liberté donne un niveau de confiance permettant
de rejeter l’hypothèse nulle que les variables sont indépendantes.

Nous allons donc calculer cette valeur de \${\chi}^2\$ pour chacune des
paires/arêtes de notre graphe de co-occurrences.

#### Traitement des arêtes

La partie la plus facile à calculer, que l’on a déjà croisée dans la séance
précédente, c’est T, le nombre total de documents. On peut l’obtenir via

In [ ]:
medline.count()

De même, il est assez facile de retrouver combien de documents contiennent
chaque concept, puisqu’on s’en est servi pour créer topicCounts. On va cependant
cette fois conserver l’information dans un RDD :

In [ ]:
topicCountsRdd = topics.map(lambda p: (p, 1)).reduceByKey(add)

Une fois que l’on a ce VertexRDD avec les nombres d’occurrences, on peut
l’utiliser pour créer un nouveau graphe, dans lequel il nous servira d’ensemble
de sommets (et l’on garde l’ensemble des arêtes précédent) :

In [ ]:
topicGraph = GraphFrame(topicCountsRdd, topicGraph.edges)

On dispose maintenant de tout ce qu’il faut pour calculer le test de
\${\chi}^2\$ pour chacune des arêtes de topicCountGraph. Il nous faut ici
combiner des informations stockées à la fois sur les sommets (le nombre de fois
que chaque sujet apparaît) ainsi que sur les arêtes (le nombre de fois qu’une
paire apparaît dans un document). GraphX nous permet d’effectuer ce type de
calculs à l’aide d’une structure de données appelée EdgeTriplet[VD, ED], qui
encapsule de l’information sur les arêtes et les sommets dans un seul objet
(avec les IDs de chaque sommet). En utilisant ce EdgeTriplet sur notre
topicCountGraph, on peut calculer le \${\chi}^2\$ ainsi :

In [ ]:
def chiSq(oo, ob, oa, t):
  nb = t - ob
  na = t - oa
  on = oa - oo
  no = ob - oo
  nn = t - no - on - oo
  inner = (oo * nn - on * no) - t / 2.0
  res = t * math.pow(inner, 2) / (oa * na * ob * nb)
  return res

```scala
def chiSq(OO: Int, OB: Int, OA: Int, T: Long): Double = {
  val NB = T - OB
  val NA = T - OA
  val ON = OA - OO
  val NO = OB - OO
  val NN = T - NO - ON - OO
  val inner = (OO * NN - ON * NO) - T / 2.0
  T * math.pow(inner, 2) / (OA * NA * OB * NB)
}
```


On peut ensuite combiner cette méthode avec l’opérateur mapTriplets, ce qui va
nous retourner la valeur du test pour chacune des paires. On pourra ensuite,
avec stats(), avoir une idée de la distribution des valeurs pour les arêtes de
notre graphe :

```scala
val chiSquaredGraph = topicCountGraph.mapTriplets(triplet => { chiSq(triplet.attr, triplet.srcAttr, triplet.dstAttr, T) })

chiSquaredGraph.edges.map(x => x.attr).stats()
```


Vous devriez observer quelque chose formaté comme ceci mais avec des valeurs différentes :

#### Exemple :

(count: 259920, mean: 546.97, stdev: 3428.85, max: 222305.79, min: 0.0)

Maintenant que l’on a calculé cette valeur, on va s’en servir pour filtrer les
arêtes qui ne semblent pas fournir d’information pertinente, selon le principe
décrit ci-dessus. Cette métrique prend des valeurs très différentes sur
l’ensemble des arêtes, et l’on peut du coup essayer d’employer un filtre très
strict pour éliminer les arêtes peu importantes.

Pour une table de contingence 2x2 dans laquelle il n’y aurait pas de relation
entre les variables, la valeur du test doit suivre une loi de \${\chi}^2\$ à
un degré de liberté. La valeur tabulée du \${\chi}^2\$ à un degré de liberté
pour 0.00001 est de 19.5, on peut essayer avec cette valeur comme limite pour
éliminer des arêtes (ce qui ne nous laissera donc que des arêtes dont on est
très sûrs qu’elles représentent des co-occurrences significatives).

Pour effectuer le filtrage, on utilise la méthode subgraph, qui requiert en
paramètre une fonction (anonyme) retournant un booléen à partir d’un
EdgeTriplet, pour déterminer quelles arêtes sont à préserver.

```scala
val interesting = chiSquaredGraph.subgraph(triplet => triplet.attr > 19.5)
interesting.edges.count
```


#### Question :

Quelle fraction (approximative) des nœuds a-t-on filtré ? Qu’en concluez-vous ?

Dans la section suivante, on examine l’impact de ce filtrage sur la structure de
notre graphe.

#### Analyse du graphe filtré

Commencez par réutiliser la méthode qui nous avait permis d’obtenir les
composantes connexes auparavant :

```scala
val interestingComponentCounts = sortedConnectedComponents(interesting.connectedComponents())
println(s"Nb composantes connexes : ${interestingComponentCounts.size}\n")
```


Puis, comme précédemment, regardez le top10 :

```scala
interestingComponentCounts.take(10).foreach(println)
```


#### Question :

Qu’obtenez-vous ? Qu’en concluez-vous ?

Intéressez-vous ensuite à la distribution de degrés, avec des commandes
similaires à ce qu’on avait vu précédemment :

```scala
val interestingDegrees = interesting.degrees.cache()
interestingDegrees.map(_._2).stats()
```


Ce qui doit donner (quelque chose comme) :

```scala
(count: 12062, mean: 28.30, stdev: 44.84, max: 1603.0, min: 1.0)
```


#### Question :

Qu’obtenez-vous ? Qu’en concluez-vous ?

Regardez ce qu’il s’est passé pour le « top 10 » des nœuds de plus forts degrés :

```scala
topNamesAndDegrees(interestingDegrees, topicGraph).foreach(println)
```


#### Conclusion sur cette partie

Notre filtrage à partir d’un test d’indépendance du \\\\( {\chi}^2 \\\\)
a eu l’effet escompté : il nous a permis d’éliminer les arêtes de notre graphe
qui reliaient des concepts génériques entre eux, en préservant les
associations porteuses d’information. Bien entendu, il serait maintenant
intéressant d’explorer différentes valeurs de filtrage, pour voir l’impact
qu’elles peuvent avoir sur la connexité du graphe et la distribution de
degrés. Il existe peut-être une valeur particulière à partir de laquelle la
composante connexe « éclate » en petites parties, à moins qu’elle ne « fonde »
progressivement, comme un gigantesque iceberg…

## Réseaux Petits Mondes : Cliques et coefficients de clustering

On dit qu’un graphe est complet si chaque sommet est connecté à chacun des
autres par une arête. Dans un graphe \\\\( G \\\\) quelconque, il peut exister des
sous-ensembles de nœuds induisant un sous-graphe complet de \\\\( G \\\\) : on
appelle cet ensemble de sommet une clique. La présence de cliques de grande
taille dans un graphe indique qu’il possède une structure locale similaire aux
grands réseaux réels. Cependant, trouver des cliques est un problème
NP-difficile (donc on ne sait pas en général trouver de solution en temps
raisonnable). On a donc développé des métriques moins coûteuses pour estimer la
densité locale, comme le calcul du nombre de triangles à un sommet. Un triangle
est simplement un graphe complet de trois sommets et le nombre de triangles au
sommet \\\\( V \\\\) est le nombre de triangles contenant \\\\( V \\\\) ce qui permet
d’estimer si les voisins de \\\\( V \\\\) sont connectés entre eux. Watts et
Strogatz ont ainsi défini le coefficient de clustering local, la fraction du
nombre de triangles existants et du nombre total de triangles possibles. Pour
un sommet \\\\( V \\\\) avec \\\\( k \\\\) voisins et
\\\\( t \\\\) triangles, \\\\( C \\\\) vaut :

$$
C(V) = \frac{2 * t}{k(k-1)}
$$

On peut utiliser GraphX pour calculer ce coefficient de clustering sur le graphe
que l’on a construit, grâce à la méthode triangleCount fournie.

```scala
val triCountGraph = topicGraph.triangleCount()
triCountGraph.vertices.map(x => x._2).stats()
```


Cela nous permet d’obtenir le numérateur du coefficient de clustering pour
chaque nœud. Pour le dénominateur, il nous faut connaître le nombre total de
triangles possibles contenant chaque sommet. Rappelez-vous que ce nombre vaut
$ n(n-1)/2 $ si $ n $ est le nombre de voisins du noeud. On peut donc
effectuer le calcul à pour chaque nœud :

```scala
val maxTrisGraph = topicGraph.degrees.mapValues(d => d * (d - 1) / 2.0)
```


Avec triCountGraph et maxTrisGraph (ce sont des VertexRDD), on peut donc
calculer le coefficient de clustering pour chaque nœud :

```scala
val clusterCoefGraph = triCountGraph.vertices.innerJoin(maxTrisGraph) {
  (vertexId, triCount, maxTris) => {
    if (maxTris == 0) 0
    else triCount / maxTris
  }
}
```


Ce qui nous intéresse maintenant, c’est le coefficient de clustering moyen de ce
graphe :

```scala
clusterCoefGraph.map(_._2).sum() / topicGraph.vertices.count()
```


>**Note**
>
>Question : Qu’observez-vous ? Qu’en concluez-vous ?

## Question :

Qu’observez-vous ? Qu’en concluez-vous ?

## Bibliographie

Karau, H., A. Konwinski, P. Wendell et M. Zaharia, *Learning Spark*, O’Reilly, 2015.

Ryza, S., U. Laserson, S. Owen and J. Wills, *Advanced Analytics with Spark*, O’Reilly, 2010.

Large-Scale Structure of a Network of Co-Occurring MeSH Terms: Statistical
Analysis of Macroscopic Properties, by Kastrin et al. (2014),